## 1.1. Probability Distributions Analysis for Target Variables

This notebook contains the analysis of variables the initial processing of the data in `data/processed/dataset.csv`.

In [2]:
import torch
import warnings
import numpy as np
import pandas as pd
import torch.nn as nn
import plotly.express as px
import plotly.graph_objects as go
from xgboost import XGBRegressor
from sklearn.pipeline import make_pipeline
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from youtube_trends.config import PROCESSED_DATA_DIR
from sklearn.preprocessing import PolynomialFeatures
from torch.utils.data import TensorDataset, DataLoader
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.linear_model import LinearRegression, Ridge, Lasso

import matplotlib.pyplot as plt

warnings.filterwarnings('ignore')
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [3]:
df_train = pd.read_csv(PROCESSED_DATA_DIR / "train_dataset.csv", low_memory=False)
df_val = pd.read_csv(PROCESSED_DATA_DIR / "val_dataset.csv", low_memory=False)
df_test = pd.read_csv(PROCESSED_DATA_DIR / "test_dataset.csv", low_memory=False)

In [4]:
print(df_train.shape)
print(df_val.shape)
print(df_test.shape)

(46337, 199)
(7626, 199)
(6736, 199)


In [5]:
X_train = df_train[['video_view_count']]
y_train = df_train['video_like_count']
X_val = df_val[['video_view_count']]
y_val = df_val['video_like_count']
X_test = df_test[['video_view_count']]
y_test = df_test['video_like_count']

In [6]:
models = {
    "Linear": LinearRegression(),
    "Polynomial (deg=2)": make_pipeline(PolynomialFeatures(2), LinearRegression()),
    "Ridge": Ridge(alpha=1.0),
    "Lasso": Lasso(alpha=0.1),
    "Decision Tree": DecisionTreeRegressor(max_depth=5),
    "Random Forest": RandomForestRegressor(n_estimators=100, random_state=42),
    "XGBoost": XGBRegressor(n_estimators=100, learning_rate=0.1, random_state=42),
}

In [7]:
results = []
predictions = {}

for name, model in models.items():
    model.fit(X_train, y_train)
    pred = model.predict(X_val)
    mse = mean_squared_error(y_val, pred)
    r2 = r2_score(y_val, pred)
    results.append((name, mse, r2))
    predictions[name] = pred

In [9]:
X_train_torch = torch.tensor(X_train.values, dtype=torch.float32)
y_train_torch = torch.tensor(y_train.values, dtype=torch.float32).view(-1, 1)
X_val_torch = torch.tensor(X_val.values, dtype=torch.float32)
y_val_torch = torch.tensor(y_val.values, dtype=torch.float32).view(-1, 1)
X_test_torch = torch.tensor(X_test.values, dtype=torch.float32)
y_test_torch = torch.tensor(y_test.values, dtype=torch.float32).view(-1, 1)

train_dataset = TensorDataset(X_train_torch, y_train_torch)
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)

In [11]:
class NN(nn.Module):
    def __init__(self):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(1, 32),
            nn.ReLU(),
            nn.Linear(32, 16),
            nn.ReLU(),
            nn.Linear(16, 1)
        )

    def forward(self, x):
        return self.net(x)

In [12]:
model_nn = NN()
loss_fn = nn.MSELoss()
optimizer = torch.optim.Adam(model_nn.parameters(), lr=0.01)

In [ ]:
for epoch in range(100):
    model_nn.train()
    for xb, yb in train_loader:
        pred = model_nn(xb)
        loss = loss_fn(pred, yb)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        print(f'Epoch: {epoch+1},\t Loss: {loss}')

Epoch: 1,	 Loss: 40634904576.0
Epoch: 1,	 Loss: 44688838656.0
Epoch: 1,	 Loss: 121943908352.0
Epoch: 1,	 Loss: 17151240192.0
Epoch: 1,	 Loss: 37039947776.0
Epoch: 1,	 Loss: 59183816704.0
Epoch: 1,	 Loss: 129885126656.0
Epoch: 1,	 Loss: 94349385728.0
Epoch: 1,	 Loss: 63306592256.0
Epoch: 1,	 Loss: 22057177088.0
Epoch: 1,	 Loss: 212126384128.0
Epoch: 1,	 Loss: 68751802368.0
Epoch: 1,	 Loss: 19790778368.0
Epoch: 1,	 Loss: 166285754368.0
Epoch: 1,	 Loss: 52790636544.0
Epoch: 1,	 Loss: 147227656192.0
Epoch: 1,	 Loss: 45684174848.0
Epoch: 1,	 Loss: 150141763584.0
Epoch: 1,	 Loss: 143691431936.0
Epoch: 1,	 Loss: 227417718784.0
Epoch: 1,	 Loss: 79915720704.0
Epoch: 1,	 Loss: 92468649984.0
Epoch: 1,	 Loss: 119577321472.0
Epoch: 1,	 Loss: 21018718208.0
Epoch: 1,	 Loss: 211042222080.0
Epoch: 1,	 Loss: 288549961728.0
Epoch: 1,	 Loss: 168086683648.0
Epoch: 1,	 Loss: 274942525440.0
Epoch: 1,	 Loss: 32514936832.0
Epoch: 1,	 Loss: 166461456384.0
Epoch: 1,	 Loss: 94217650176.0
Epoch: 1,	 Loss: 33084119

In [ ]:
model_nn.eval()
with torch.no_grad():
    y_pred_nn = model_nn(X_val_torch).numpy().flatten()

In [ ]:
mse_nn = mean_squared_error(y_val, y_pred_nn)
r2_nn = r2_score(y_val, y_pred_nn)
results.append(("Neural Network (PyTorch)", mse_nn, r2_nn))
predictions["Neural Network (PyTorch)"] = y_pred_nn

In [ ]:
df_results = pd.DataFrame(results, columns=["Model", "MSE", "R^2"])
print(df_results)

In [9]:
import pandas as pd
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score


In [10]:
# Entrenamiento
X_train = df_train[['video_view_count']]
y_train = df_train['video_like_count']

# Validación
X_val = df_val[['video_view_count']]
y_val = df_val['video_like_count']

# Test
X_test = df_test[['video_view_count']]
y_test = df_test['video_like_count']

In [ ]:
model = LinearRegression()
model.fit(X_train, y_train)

LinearRegression()

In [13]:
# Predicción en validación
y_pred_val = model.predict(X_val)

# Métricas
mse = mean_squared_error(y_val, y_pred_val)
r2 = r2_score(y_val, y_pred_val)

print(f"MSE en validación: {mse:.2f}")
print(f"R^2 en validación: {r2:.2f}")


MSE en validación: 369391598087.16
R^2 en validación: 0.70


In [14]:
y_pred_test = model.predict(X_test)

# Métricas de test
mse_test = mean_squared_error(y_test, y_pred_test)
r2_test = r2_score(y_test, y_pred_test)

print(f"MSE en test: {mse_test:.2f}")
print(f"R^2 en test: {r2_test:.2f}")


MSE en test: 49368575316.73
R^2 en test: 0.69


In [15]:
import matplotlib.pyplot as plt

plt.figure(figsize=(8,5))
plt.scatter(X_test, y_test, color='blue', label='Datos reales')
plt.plot(X_test, y_pred_test, color='red', label='Predicción')
plt.xlabel('Video View Count')
plt.ylabel('Video Like Count')
plt.title('Regresión Lineal: Likes vs Views')
plt.legend()
plt.grid(True)
plt.show()


#### Target variables

In [9]:
df_target = df[['video_view_count', 'video_like_count', 'days_to_trend']]
display(df_target)

video_view_count  video_like_count  days_to_trend
0               494385.0           27082.0            0.0
1               494385.0           27082.0            0.0
2               494385.0           27085.0            0.0
3               494385.0           27085.0            0.0
4               494390.0           27101.0            0.0
...                  ...               ...            ...
365673        11083286.0          531011.0           11.0
365674         8809957.0          480523.0            1.0
365675        11220403.0          533037.0           13.0
365676        11286966.0          534167.0           14.0
365677         7650474.0          449952.0            0.0

[365678 rows x 3 columns]

In [11]:
df_target.describe()

video_view_count  video_like_count  days_to_trend
count      3.656780e+05      3.656780e+05  365678.000000
mean       1.251095e+07      3.554401e+05       8.363905
std        2.699039e+07      7.737553e+05       7.053836
min        5.299000e+03      0.000000e+00       0.000000
25%        5.939315e+05      1.721625e+04       3.000000
50%        2.054774e+06      6.405350e+04       6.000000
75%        1.139406e+07      3.128022e+05      12.000000
max        2.906813e+08      8.339166e+06      36.000000

In [12]:
correlation_matrix = df_target.corr(numeric_only=True)
correlation_matrix

video_view_count  video_like_count  days_to_trend
video_view_count          1.000000          0.837456       0.268759
video_like_count          0.837456          1.000000       0.241172
days_to_trend             0.268759          0.241172       1.000000

In [13]:
fig = go.Figure(data=go.Heatmap(
    z=correlation_matrix.loc[correlation_matrix.columns[::-1], correlation_matrix.columns].values, 
    x=correlation_matrix.columns,  
    y=correlation_matrix.columns[::-1],  
    colorscale='Blues',  
    colorbar=dict(title="Correlation"),  
    hoverongaps=True, 
    zmin=-1,  
    zmax=1,   
))

annotations = []
for i in range(len(correlation_matrix.columns)):
    for j in range(len(correlation_matrix.columns)):
        value = correlation_matrix.loc[correlation_matrix.columns[j], correlation_matrix.columns[i]]
        text_color = "black" if abs(value) < 0.5 else "white"  
        annotations.append(
            dict(
                x=correlation_matrix.columns[i],  
                y=correlation_matrix.columns[j], 
                text=f"{value:.2f}", 
                showarrow=False,
                font=dict(size=12, color=text_color),
                align="center"
            )
        )

fig.update_layout(
    title="Correlation Matrix",
    xaxis=dict(title="Variables", tickangle=45), 
    yaxis=dict(title="Variables"),  
    height=900,  
    width=900,   
    annotations=annotations  
)

fig.show() 

In [14]:
fig = px.scatter(
    df,
    x='video_view_count',
    y='video_like_count',
    title='Relationship Between Video Views and Likes',
    labels={
        'video_view_count': 'View Count',
        'video_like_count': 'Like Count'
    },
    template='plotly_white'
)

fig.show()

In [4]:
# Regression Models for Predicting YouTube Video Likes from Views

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.linear_model import LinearRegression, Ridge, Lasso
from sklearn.preprocessing import PolynomialFeatures
from sklearn.pipeline import make_pipeline
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader

# --- Load your data here ---
# df_train, df_val, df_test must already be loaded with columns:
# 'video_view_count' and 'video_like_count'

# --- Feature and target ---
X_train = df_train[['video_view_count']]
y_train = df_train['video_like_count']
X_val = df_val[['video_view_count']]
y_val = df_val['video_like_count']

# --- Regression Models ---
models = {
    "Linear": LinearRegression(),
    "Polynomial (deg=2)": make_pipeline(PolynomialFeatures(2), LinearRegression()),
    "Ridge": Ridge(alpha=1.0),
    "Lasso": Lasso(alpha=0.1),
    "Decision Tree": DecisionTreeRegressor(max_depth=5),
    "Random Forest": RandomForestRegressor(n_estimators=100, random_state=42),
    "XGBoost": XGBRegressor(n_estimators=100, learning_rate=0.1, random_state=42),
}

results = []
predictions = {}

for name, model in models.items():
    model.fit(X_train, y_train)
    pred = model.predict(X_val)
    mse = mean_squared_error(y_val, pred)
    r2 = r2_score(y_val, pred)
    results.append((name, mse, r2))
    predictions[name] = pred

# --- Neural Network with PyTorch ---
X_train_torch = torch.tensor(X_train.values, dtype=torch.float32)
y_train_torch = torch.tensor(y_train.values, dtype=torch.float32).view(-1, 1)
X_val_torch = torch.tensor(X_val.values, dtype=torch.float32)
y_val_torch = torch.tensor(y_val.values, dtype=torch.float32).view(-1, 1)

train_dataset = TensorDataset(X_train_torch, y_train_torch)
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)

class DenseNN(nn.Module):
    def __init__(self):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(1, 32),
            nn.ReLU(),
            nn.Linear(32, 16),
            nn.ReLU(),
            nn.Linear(16, 1)
        )

    def forward(self, x):
        return self.net(x)

model_nn = DenseNN()
loss_fn = nn.MSELoss()
optimizer = torch.optim.Adam(model_nn.parameters(), lr=0.01)

for epoch in range(100):
    model_nn.train()
    for xb, yb in train_loader:
        pred = model_nn(xb)
        loss = loss_fn(pred, yb)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

model_nn.eval()
with torch.no_grad():
    y_pred_nn = model_nn(X_val_torch).numpy().flatten()

mse_nn = mean_squared_error(y_val, y_pred_nn)
r2_nn = r2_score(y_val, y_pred_nn)
results.append(("Neural Network (PyTorch)", mse_nn, r2_nn))
predictions["Neural Network (PyTorch)"] = y_pred_nn

# --- Results Table ---
df_results = pd.DataFrame(results, columns=["Model", "MSE", "R^2"])
print(df_results)

# --- Visualize Predictions ---
plt.figure(figsize=(14, 8))
plt.scatter(X_val, y_val, color='black', alpha=0.3, label='True Values')

for name, pred in predictions.items():
    plt.scatter(X_val, pred, label=name, alpha=0.6)

plt.xlabel("Video View Count")
plt.ylabel("Video Like Count")
plt.legend()
plt.title("Model Predictions on Validation Set")
plt.grid(True)
plt.show()

# --- Bar Plot of R^2 Scores ---
plt.figure(figsize=(10, 5))
plt.bar(df_results['Model'], df_results['R^2'], color='skyblue')
plt.ylabel("R^2 Score")
plt.title("Comparison of R^2 Scores Across Models")
plt.xticks(rotation=45)
plt.grid(True, axis='y')
plt.tight_layout()
plt.show()


ModuleNotFoundError: No module named 'xgboost'